In [1]:
import os
import sys

import numpy as np
import pandas as pd
from sqlalchemy import create_engine


sys.path.append(os.path.dirname(os.path.abspath(os.path.dirname('../..'))))
from strategy import EquityStrategy
from tester import Tester


base_path = os.path.abspath('../../..')
data_path = os.path.join(base_path, 'data')
database_path = os.path.join(data_path, 'database')
strategy_path = os.path.join(base_path, 'strategy')
check_path = os.path.join(strategy_path, 'check')
sys.path.append(strategy_path)

In [22]:
import os
import sys
import numpy as np
import pandas as pd
pd.set_option('display.max_columns', 50)

from matplotlib import pyplot as plt
import seaborn as sns
%matplotlib inline

import plotly
import plotly.graph_objs as go
import cufflinks as cf
cf.set_config_file(offline=True)

In [2]:
from strategy import CommodityStrategy, EquityStrategy, IRStrategy, EmergingStrategy
from tester import Tester

In [3]:
eindex_path = os.path.join(data_path, 'totindex.csv')
eindex1_path = os.path.join(data_path, 'priceindex.csv')
efuture_path = os.path.join(data_path, 'FutGenratio1.csv')

In [4]:
total_ret_idx = pd.read_csv(eindex_path, header=0, index_col=0, parse_dates=True)
total_ret = total_ret_idx.pct_change(1)
prc_idx = pd.read_csv(eindex1_path, header=0, index_col=0, parse_dates=True)
prc_ret = prc_idx.pct_change(1)
fut_idx = pd.read_csv(efuture_path, header=0, index_col=0, parse_dates=True)
#fut_idx.index = pd.to_datetime(fut_idx.index, unit='D', origin=pd.Timestamp('1899-12-30'))
fut_ret = fut_idx.pct_change(1)

# 만약에 eindex에 빈 정보가 있으면 eindex1으로 대체
no_data_dates = total_ret[(total_ret.isnull().sum(axis=1) > 0).values].index
total_ret.loc[no_data_dates] = prc_ret.loc[no_data_dates]

# 2007년까지는 eindex 2008년부터는 future 사용
ERet = pd.concat([total_ret.loc[:'2007-12-31'], fut_ret.loc['2008-01-01':]], axis=0)
ERet.fillna(0, inplace=True)
Eindex = (1. + ERet).cumprod()

ERet.index.name = 'tdate'
Eindex.index.name = 'tdate'

ERet.columns.name = 'ticker'
Eindex.columns.name = 'ticker'

In [5]:
growthvalue = pd.read_csv(os.path.join(data_path, "growthvalue.csv"), index_col=0, parse_dates=True)
growthvalue.index.name = 'tdate'
growthvalue.columns.name = 'ticker'

In [6]:
minobs1=12
nopos=0.4
CS=0.35
longlen=12
shortlen=0
SDEV=12

In [7]:
i = 0

In [8]:
ret = ERet
index = Eindex

In [9]:
class EFX(EquityStrategy):
    def __init__(self, strategy_name, asset_type):
        super().__init__(strategy_name=strategy_name, asset_type=asset_type)
        self.fx = None

    def load_strategy_data(self, table='bloom', origin='fx'):
        self.fx = self._load_strategy_data(table=table, origin=origin)

    def calculate_signal(self, minobs1=12, nopos=0.4, CS=0.35, longlen=12, shortlen=0, SDEV=12):
        """

        :param cs_num: percentage of position for cross sectional signal
        :param min_obs:
        :param longlen: long term price momentum period
        :param shortlen: short term price momentum period
        :return:
        """
        self.logger.info('[STEP 3] CACULATE SIGNAL')

        for i in range(2):
            if i == 0:
                RET = self.ret.loc[:, ['SPX', 'TSX', 'FTSE', 'DAX', 'CAC', 'SMI', 'MIB', 'IBEX', 'OMX', 'AEX']]
            else:
                RET = self.ret.loc[:, ['NKY', 'AS51', 'HSI', "SG"]]

            index = self.index[RET.columns]
            fx = self.fx
            fx = fx[index.columns]

            # 3. Signal 1. Reverse of FX Strength
            Mag = fx.iloc[longlen - shortlen:].to_numpy() / fx[:-(longlen - shortlen)].to_numpy() - 1
            Mag = pd.DataFrame(Mag, columns=fx.columns)
            Mag.index = fx.index[longlen:]
            RV = -1 * Mag

            # 3-1. Rank
            pctrank = lambda x: pd.Series(x).rank(pct=True).iloc[-1]
            RVrank = RV.expanding().apply(pctrank, raw=True)  # it takes some time
            RVrank = RVrank.iloc[minobs1 - 1:, ]

            # 3-2. Long Short
            RV1 = RV.iloc[minobs1 - 1:]
            truecount = (RV1.notnull().sum(axis=1) * CS).apply(round)

            CSRV = (RV1).rank(axis=1, method='first')  # Short
            CSRV1 = (-1 * RV1).rank(axis=1, method='first')  # Long

            CSRVpos = CSRV.fillna(0) * 0
            CSRVpos[CSRV.apply(lambda x: x <= truecount, axis=0)] = -1
            CSRVpos[CSRV1.apply(lambda x: x <= truecount, axis=0)] = 1

            # Final CS signal
            Magrank = RVrank
            CSMagpos = CSRVpos

            # Signal2. Reverse of FX Strength / 12 month STDEV
            ret = fx.iloc[1:].to_numpy() / fx[:-1].to_numpy() - 1
            ret = pd.DataFrame(ret, columns=fx.columns)
            ret.index = fx.index[1:]

            STDEV = ret.rolling(SDEV).std() * np.sqrt(12)
            STDEV1 = STDEV.iloc[longlen - 1:]
            RV = (-1 * Mag) / STDEV1
            RV1 = RV.iloc[minobs1 - 1:]

            # 4. Rank
            pctrank = lambda x: pd.Series(x).rank(pct=True).iloc[-1]
            RVrank = RV.expanding().apply(pctrank, raw=True)  # it takes some time
            RVrank = RVrank.iloc[minobs1 - 1:, ]

            # 5. Long Short
            truecount = (RV1.notnull().sum(axis=1) * CS).apply(round)

            # 1. Cross sectional
            CSRV = (RV1).rank(axis=1, method='first')
            CSRV1 = (-RV1).rank(axis=1, method='first')

            CSRVpos = CSRV.fillna(0) * 0
            CSRVpos[CSRV.apply(lambda x: x <= truecount, axis=0)] = -1
            CSRVpos[CSRV1.apply(lambda x: x <= truecount, axis=0)] = 1

            # Final CS signal
            Relrank = RVrank
            CSRelpos = CSRVpos
            CSRV = CSRelpos * 1 / 2 + CSMagpos * 1 / 2

            # 2. Time Series
            TSRV1 = Magrank.fillna(0) * 0
            TSRV1[Magrank > nopos + (1 - nopos) / 2] = 1  # Long
            TSRV1[Magrank < (1 - nopos) / 2] = -1  # Short

            TSRV2 = Relrank.fillna(0) * 0
            TSRV2[Relrank > nopos + (1 - nopos) / 2] = 1  # Long
            TSRV2[Relrank < (1 - nopos) / 2] = -1  # Short
            TSRV = 1 / 2 * TSRV1 + 1 / 2 * TSRV2

            if i == 0:
                TSRVrun1 = TSRV
                CSRVrun1 = CSRV
            else:
                TSRVrun2 = TSRV
                CSRVrun2 = CSRV

        TSRV = pd.concat([TSRVrun1, TSRVrun2], axis=1)
        CSRV = pd.concat([CSRVrun1, CSRVrun2], axis=1)

        TSRV = TSRV[self.ret.columns]
        CSRV = CSRV[self.ret.columns]

        self.TSRV = TSRV.loc[self.ret.index].fillna(method='ffill').dropna(how='all')
        self.CSRV = CSRV.loc[self.ret.index].fillna(method='ffill').dropna(how='all')

        # Align dates with each other
        if self.TSRV.index[0] > self.CSRV.index[0]:
            self.CSRV = self.CSRV.loc[self.TSRV.index[0]:]
        else:
            self.TSRV = self.TSRV.loc[self.CSRV.index[0]:]

In [12]:
efx = EFX(strategy_name="EFX", asset_type="EQUITY")
efx.index = Eindex.copy()
efx.ret = ERet.copy()
# efx.load_index_and_return(from_db=False, save_file=False)

fx = pd.read_csv(os.path.join(data_path, "fx.csv"), index_col=0, parse_dates=True)
fx.index.name = 'tdate'
fx.columns.name = 'ticker'

efx.fx = fx
# efx.load_strategy_data(table='bloom', origin='fx')
efx.set_rebalance_period(ts_freq='month', cs_freq='month')
efx.calculate_signal(minobs1=12, nopos=0.4, CS=0.35, longlen=12, shortlen=0, SDEV=12)

2019-12-27 13:51:13,893 - EFX - INFO - [STEP 0] START LOGGING EFX
2019-12-27 13:51:13,893 - EFX - INFO - [STEP 0] START LOGGING EFX
2019-12-27 13:51:13,899 - EFX - INFO - [STEP 2] SET REBALANCE PERIOD
2019-12-27 13:51:13,899 - EFX - INFO - [STEP 2] SET REBALANCE PERIOD
2019-12-27 13:51:13,900 - EFX - INFO - [STEP 3] CACULATE SIGNAL
2019-12-27 13:51:13,900 - EFX - INFO - [STEP 3] CACULATE SIGNAL
C:\ProgramData\Anaconda3\lib\site-packages\ipykernel_launcher.py:110: FutureWarning: 
Passing list-likes to .loc or [] with any missing label will raise
KeyError in the future, you can use .reindex() as an alternative.

See the documentation here:
https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#deprecate-loc-reindex-listlike
C:\ProgramData\Anaconda3\lib\site-packages\ipykernel_launcher.py:111: FutureWarning: 
Passing list-likes to .loc or [] with any missing label will raise
KeyError in the future, you can use .reindex() as an alternative.

See the documentation here:
https

In [14]:
efx_TSRV = pd.read_csv('../past/efx_tsrv.csv', index_col=[0])
efx_CSRV = pd.read_csv('../past/efx_csrv.csv', index_col=[0])

efx_TSRV.index = pd.to_datetime(efx_TSRV.index)
efx_CSRV.index = pd.to_datetime(efx_CSRV.index)

In [15]:
TSRV_DIFF = (efx_TSRV - efx.TSRV)

In [16]:
TSRV_DIFF[np.abs(TSRV_DIFF) > 0.01].count()

SPX     0
TSX     0
FTSE    0
DAX     0
CAC     0
SMI     0
MIB     0
IBEX    0
OMX     0
AEX     0
NKY     0
AS51    0
HSI     0
SG      0
dtype: int64

In [18]:
CSRV_DIFF = (efx_CSRV - efx.CSRV)

In [19]:
CSRV_DIFF[np.abs(CSRV_DIFF) > 0.01].count()

SPX       0
TSX       0
FTSE      0
DAX     956
CAC     956
SMI       0
MIB       0
IBEX      0
OMX       0
AEX       0
NKY       0
AS51      0
HSI       0
SG        0
dtype: int64

In [23]:
CSRV_DIFF.iplot()

In [24]:
efx.CSRV

ticker      SPX  TSX  FTSE  DAX  CAC  SMI  MIB  IBEX  OMX  AEX  NKY  AS51  \
tdate                                                                       
1989-12-29 -1.0 -0.5   1.0 -0.5  0.0  1.0  0.0   0.0  0.0  0.0  1.0   0.0   
1990-01-01 -1.0 -0.5   1.0 -0.5  0.0  1.0  0.0   0.0  0.0  0.0  1.0   0.0   
1990-01-02 -1.0 -0.5   1.0 -0.5  0.0  1.0  0.0   0.0  0.0  0.0  1.0   0.0   
1990-01-03 -1.0 -0.5   1.0 -0.5  0.0  1.0  0.0   0.0  0.0  0.0  1.0   0.0   
1990-01-04 -1.0 -0.5   1.0 -0.5  0.0  1.0  0.0   0.0  0.0  0.0  1.0   0.0   
...         ...  ...   ...  ...  ...  ...  ...   ...  ...  ...  ...   ...   
2018-05-03  1.0  0.0   0.0 -1.0 -1.0  1.0  0.0   0.0  0.0  0.0  0.0   0.0   
2018-05-04  1.0  0.0   0.0 -1.0 -1.0  1.0  0.0   0.0  0.0  0.0  0.0   0.0   
2018-05-07  1.0  0.0   0.0 -1.0 -1.0  1.0  0.0   0.0  0.0  0.0  0.0   0.0   
2018-05-08  1.0  0.0   0.0 -1.0 -1.0  1.0  0.0   0.0  0.0  0.0  0.0   0.0   
2018-05-09  1.0  0.0   0.0 -1.0 -1.0  1.0  0.0   0.0  0.0  0.0  0.0   0.0   

ticker      HSI   SG  
tdate                 
1989-12-29 -0.5 -0.5  
1990-01-01 -0.5 -0.5  
1990-01-02 -0.5 -0.5  
1990-01-03 -0.5 -0.5  
1990-01-04 -0.5 -0.5  
...         ...  ...  
2018-05-03  1.0 -1.0  
2018-05-04  1.0 -1.0  
2018-05-07  1.0 -1.0  
2018-05-08  1.0 -1.0  
2018-05-09  1.0 -1.0  

[7399 rows x 14 columns]

In [25]:
i = 0

In [26]:
ret = ERet
index = Eindex
fx = fx

In [27]:
if i == 0:
    RET = ret.loc[:, ['SPX', 'TSX', 'FTSE', 'DAX', 'CAC', 'SMI', 'MIB', 'IBEX', 'OMX', 'AEX']]
else:
    RET = ret.loc[:, ['NKY', 'AS51', 'HSI', "SG"]]

index = index[RET.columns]
fx = fx
fx = fx[index.columns]

# 3. Signal 1. Reverse of FX Strength
Mag = fx.iloc[longlen - shortlen:].to_numpy() / fx[:-(longlen - shortlen)].to_numpy() - 1
Mag = pd.DataFrame(Mag, columns=fx.columns)
Mag.index = fx.index[longlen:]
RV = -1 * Mag

In [30]:
efx.CSRV.head()

ticker      SPX  TSX  FTSE  DAX  CAC  SMI  MIB  IBEX  OMX  AEX  NKY  AS51  \
tdate                                                                       
1989-12-29 -1.0 -0.5   1.0 -0.5  0.0  1.0  0.0   0.0  0.0  0.0  1.0   0.0   
1990-01-01 -1.0 -0.5   1.0 -0.5  0.0  1.0  0.0   0.0  0.0  0.0  1.0   0.0   
1990-01-02 -1.0 -0.5   1.0 -0.5  0.0  1.0  0.0   0.0  0.0  0.0  1.0   0.0   
1990-01-03 -1.0 -0.5   1.0 -0.5  0.0  1.0  0.0   0.0  0.0  0.0  1.0   0.0   
1990-01-04 -1.0 -0.5   1.0 -0.5  0.0  1.0  0.0   0.0  0.0  0.0  1.0   0.0   

ticker      HSI   SG  
tdate                 
1989-12-29 -0.5 -0.5  
1990-01-01 -0.5 -0.5  
1990-01-02 -0.5 -0.5  
1990-01-03 -0.5 -0.5  
1990-01-04 -0.5 -0.5

In [ ]:

# 3-1. Rank
pctrank = lambda x: pd.Series(x).rank(pct=True).iloc[-1]
RVrank = RV.expanding().apply(pctrank, raw=True)  # it takes some time
RVrank = RVrank.iloc[minobs1 - 1:, ]

# 3-2. Long Short
RV1 = RV.iloc[minobs1 - 1:]
truecount = (RV1.notnull().sum(axis=1) * CS).apply(round)

CSRV = (RV1).rank(axis=1, method='first')  # Short
CSRV1 = (-1 * RV1).rank(axis=1, method='first')  # Long

CSRVpos = CSRV.fillna(0) * 0
CSRVpos[CSRV.apply(lambda x: x <= truecount, axis=0)] = -1
CSRVpos[CSRV1.apply(lambda x: x <= truecount, axis=0)] = 1

# Final CS signal
Magrank = RVrank
CSMagpos = CSRVpos

# Signal2. Reverse of FX Strength / 12 month STDEV
ret = fx.iloc[1:].to_numpy() / fx[:-1].to_numpy() - 1
ret = pd.DataFrame(ret, columns=fx.columns)
ret.index = fx.index[1:]

STDEV = ret.rolling(SDEV).std() * np.sqrt(12)
STDEV1 = STDEV.iloc[longlen - 1:]
RV = (-1 * Mag) / STDEV1
RV1 = RV.iloc[minobs1 - 1:]

# 4. Rank
pctrank = lambda x: pd.Series(x).rank(pct=True).iloc[-1]
RVrank = RV.expanding().apply(pctrank, raw=True)  # it takes some time
RVrank = RVrank.iloc[minobs1 - 1:, ]

# 5. Long Short
truecount = (RV1.notnull().sum(axis=1) * CS).apply(round)

# 1. Cross sectional
CSRV = (RV1).rank(axis=1, method='first')
CSRV1 = (-RV1).rank(axis=1, method='first')

CSRVpos = CSRV.fillna(0) * 0
CSRVpos[CSRV.apply(lambda x: x <= truecount, axis=0)] = -1
CSRVpos[CSRV1.apply(lambda x: x <= truecount, axis=0)] = 1

# Final CS signal
Relrank = RVrank
CSRelpos = CSRVpos
CSRV = CSRelpos * 1 / 2 + CSMagpos * 1 / 2

# 2. Time Series
TSRV1 = Magrank.fillna(0) * 0
TSRV1[Magrank > nopos + (1 - nopos) / 2] = 1  # Long
TSRV1[Magrank < (1 - nopos) / 2] = -1  # Short

TSRV2 = Relrank.fillna(0) * 0
TSRV2[Relrank > nopos + (1 - nopos) / 2] = 1  # Long
TSRV2[Relrank < (1 - nopos) / 2] = -1  # Short
TSRV = 1 / 2 * TSRV1 + 1 / 2 * TSRV2

if i == 0:
    TSRVrun1 = TSRV
    CSRVrun1 = CSRV
else:
    TSRVrun2 = TSRV
    CSRVrun2 = CSRV
